In [1]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.metrics import r2_score
from sklearn.model_selection import GridSearchCV
from sklearn.linear_model import LinearRegression
from sklearn.tree import DecisionTreeRegressor
from sklearn.ensemble import RandomForestRegressor
from sklearn.cluster import KMeans
import datetime as dt

In [2]:
data= pd.read_csv("./Dataset/Salary Prediction of Data Professions.csv")

In [3]:
data.head()

FIRST NAME   LAST NAME SEX         DOJ CURRENT DATE DESIGNATION   AGE  \
0     TOMASA       ARMEN   F   5-18-2014   01-07-2016     Analyst  21.0   
1      ANNIE         NaN   F         NaN   01-07-2016   Associate   NaN   
2      OLIVE        ANCY   F   7-28-2014   01-07-2016     Analyst  21.0   
3     CHERRY     AQUILAR   F  04-03-2013   01-07-2016     Analyst  22.0   
4       LEON  ABOULAHOUD   M  11-20-2014   01-07-2016     Analyst   NaN   

   SALARY        UNIT  LEAVES USED  LEAVES REMAINING  RATINGS  PAST EXP  
0   44570     Finance         24.0               6.0      2.0         0  
1   89207         Web          NaN              13.0      NaN         7  
2   40955     Finance         23.0               7.0      3.0         0  
3   45550          IT         22.0               8.0      3.0         0  
4   43161  Operations         27.0               3.0      NaN         3

In [4]:
x = data.drop(['FIRST NAME','LAST NAME','SALARY'], axis = 1)
y = data['SALARY']

In [5]:
x.shape, y.shape

((2639, 10), (2639,))

In [6]:
x['SEX'].nunique(), x['SEX'].unique() # check how many to encode
x = pd.get_dummies(x, columns=['SEX', 'DESIGNATION', 'UNIT'])

In [7]:
type(x['LEAVES REMAINING'][0])

numpy.float64

In [8]:
x['DOJ'] = pd.to_datetime(x['DOJ'])
x['CURRENT DATE'] = pd.to_datetime(x['CURRENT DATE'])

In [9]:
x['DOJ'].fillna(x['DOJ'].mean(), inplace=True)
x['CURRENT DATE'].fillna(x['CURRENT DATE'].mean(), inplace=True)
x['AGE'].fillna(x['AGE'].mean(), inplace=True)
x['RATINGS'].fillna(round(x['RATINGS'].mean()), inplace=True)
x['LEAVES USED'].fillna(30 - x['LEAVES REMAINING'], inplace=True)
x['LEAVES REMAINING'].fillna(30 - x['LEAVES USED'], inplace=True)

In [10]:
x['DOJ'] = x['DOJ'].map(dt.datetime.toordinal)
x['CURRENT DATE'] = x['CURRENT DATE'].map(dt.datetime.toordinal)

In [11]:
x.head()

DOJ  CURRENT DATE        AGE  LEAVES USED  LEAVES REMAINING  RATINGS  \
0  735371        735970  21.000000         24.0               6.0      2.0   
1  735169        735970  24.756449         17.0              13.0      3.0   
2  735442        735970  21.000000         23.0               7.0      3.0   
3  734961        735970  22.000000         22.0               8.0      3.0   
4  735557        735970  24.756449         27.0               3.0      3.0   

   PAST EXP  SEX_F  SEX_M  DESIGNATION_Analyst  ...  DESIGNATION_Director  \
0         0   True  False                 True  ...                 False   
1         7   True  False                False  ...                 False   
2         0   True  False                 True  ...                 False   
3         0   True  False                 True  ...                 False   
4         3  False   True                 True  ...                 False   

   DESIGNATION_Manager  DESIGNATION_Senior Analyst  \
0                False                       False   
1                False                       False   
2                False                       False   
3                False                       False   
4                False                       False   

   DESIGNATION_Senior Manager  UNIT_Finance  UNIT_IT  UNIT_Management  \
0                       False          True    False            False   
1                       False         False    False            False   
2                       False          True    False            False   
3                       False         False     True            False   
4                       False         False    False            False   

   UNIT_Marketing  UNIT_Operations  UNIT_Web  
0           False            False     False  
1           False            False      True  
2           False            False     False  
3           False            False     False  
4           False             True     False  

[5 rows x 21 columns]

In [12]:
X_train, X_test, y_train, y_test= train_test_split(x,y, train_size=0.8, random_state=0, shuffle=True)

In [13]:
X_train.head()

DOJ  CURRENT DATE   AGE  LEAVES USED  LEAVES REMAINING  RATINGS  \
39    735555        735970  24.0         23.0               7.0      2.0   
1503  735109        735970  21.0         22.0               8.0      4.0   
743   734883        735970  21.0         19.0              11.0      5.0   
2329  735521        735970  23.0         26.0               4.0      3.0   
2265  735219        735970  25.0         19.0              11.0      2.0   

      PAST EXP  SEX_F  SEX_M  DESIGNATION_Analyst  ...  DESIGNATION_Director  \
39           2  False   True                 True  ...                 False   
1503         0  False   True                 True  ...                 False   
743          0   True  False                 True  ...                 False   
2329         1  False   True                 True  ...                 False   
2265         2  False   True                 True  ...                 False   

      DESIGNATION_Manager  DESIGNATION_Senior Analyst  \
39                  False                       False   
1503                False                       False   
743                 False                       False   
2329                False                       False   
2265                False                       False   

      DESIGNATION_Senior Manager  UNIT_Finance  UNIT_IT  UNIT_Management  \
39                         False         False     True            False   
1503                       False         False    False            False   
743                        False         False    False            False   
2329                       False         False    False             True   
2265                       False         False    False            False   

      UNIT_Marketing  UNIT_Operations  UNIT_Web  
39             False            False     False  
1503           False            False      True  
743            False             True     False  
2329           False            False     False  
2265           False             True     False  

[5 rows x 21 columns]

In [14]:
##linear regression model

def Linear_regression(x_train,y_train,x_test,y_test):  
    lr=LinearRegression()
    lr.fit(x_train,y_train)
    pred=lr.predict(x_test)
    return pred

LR_predicted = Linear_regression(X_train,y_train,X_test,y_test)         ##calling function

In [15]:
## function to calculate r2_score of predicted values
def r2_score_(actual_value,predicted_value):
    r2=r2_score(actual_value, predicted_value)
    return r2

r2_score_(y_test,LR_predicted)

0.9562999496726552

In [16]:
#grid search cv function

def grid_search(estimator,parameters,x,y):
    grid= GridSearchCV(estimator,param_grid=parameters)
    grid.fit(x,y)
    return grid.best_params_

In [17]:
parameters_decision_tree={
    'criterion':['squared_error', 'friedman_mse', 'absolute_error', 'poisson'],
    'max_depth':[2,4,8,10,None],
    'min_samples_split' : [2,4,8,10,20],
    'max_leaf_nodes' : [4, 8, 10,15,20],
    'splitter':['best','random'],
    'max_features':['auto','sqrt','log2'],
    'min_weight_fraction_leaf':[0.1,0.2,0.3,0.4,0.5,0.6,0.7,0.8,0.9]
}

#insert parameters and estimator in grid search function
grid_search(DecisionTreeRegressor(),parameters_decision_tree,X_train,y_train)

/home/firas_bt/anaconda3/lib/python3.11/site-packages/sklearn/tree/_classes.py:277: FutureWarning: `max_features='auto'` has been deprecated in 1.1 and will be removed in 1.3. To keep the past behaviour, explicitly set `max_features=1.0'`.
  warnings.warn(
/home/firas_bt/anaconda3/lib/python3.11/site-packages/sklearn/tree/_classes.py:277: FutureWarning: `max_features='auto'` has been deprecated in 1.1 and will be removed in 1.3. To keep the past behaviour, explicitly set `max_features=1.0'`.
  warnings.warn(
/home/firas_bt/anaconda3/lib/python3.11/site-packages/sklearn/tree/_classes.py:277: FutureWarning: `max_features='auto'` has been deprecated in 1.1 and will be removed in 1.3. To keep the past behaviour, explicitly set `max_features=1.0'`.
  warnings.warn(
/home/firas_bt/anaconda3/lib/python3.11/site-packages/sklearn/tree/_classes.py:277: FutureWarning: `max_features='auto'` has been deprecated in 1.1 and will be removed in 1.3. To keep the past behaviour, explicitly set `max_featu

{'criterion': 'squared_error',
 'max_depth': 2,
 'max_features': 'auto',
 'max_leaf_nodes': 4,
 'min_samples_split': 2,
 'min_weight_fraction_leaf': 0.1,
 'splitter': 'best'}

In [18]:
def Decision_tree_regressor_model(x_train,y_train,x_test,y_test):
    tree=DecisionTreeRegressor(criterion= 'squared_error', max_depth=2, max_features='auto', 
                                max_leaf_nodes= 4, min_samples_split = 2,
                                min_weight_fraction_leaf =  0.1,splitter='best')
    tree.fit(x_train,y_train)
    pred =tree.predict(x_test)
    return pred                           
                               
DT_predicted = Decision_tree_regressor_model(X_train,y_train,X_test,y_test)

/home/firas_bt/anaconda3/lib/python3.11/site-packages/sklearn/tree/_classes.py:277: FutureWarning: `max_features='auto'` has been deprecated in 1.1 and will be removed in 1.3. To keep the past behaviour, explicitly set `max_features=1.0'`.
  warnings.warn(


In [19]:
r2_score_(y_test,DT_predicted)

0.6761912526940972

In [20]:
parameters_random_forest={
    'n_estimators':[50,100],
    'criterion':['squared_error', 'friedman_mse', 'absolute_error', 'poisson'],
    'max_depth':[2,4,8,10,None],
    'min_samples_split' : [2,4,8,10,20],
    'max_leaf_nodes' : [4, 8, 10,15,20],
    'max_features':['sqrt','log2']
}

grid_search(RandomForestRegressor(),parameters_random_forest,X_train,y_train)

In [ ]:
def random_forest_regressor(x_train,y_train,x_test,y_test):
    forest=RandomForestRegressor(n_estimators=50,criterion= 'absolute_error', max_depth=8,
                                 max_features='sqrt', max_leaf_nodes= 20, 
                                 min_samples_split = 4)
    forest.fit(x_train,y_train)
    pred =forest.predict(x_test)
    return pred 

RF_predicted=random_forest_regressor(X_train,y_train,X_test,y_test)

In [ ]:
r2_score_(y_test,RF_predicted)

In [ ]:
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D

fig = plt.figure(figsize=(10,10))
ax = fig.add_subplot(111,projection="3d")
ax.scatter(data['UNIT'],data['DESIGNATION'],data['SALARY'])
plt.show()

In [ ]:
k_range = range(1, 10)   #considering a range of 10 clusters

# Compute the sum of squared distances (SSE) for each value of k
sse = []
for k in k_range:
    kmeans = KMeans(n_clusters=k, random_state=0)
    kmeans.fit(x)
    sse.append(kmeans.inertia_)

In [ ]:
plt.plot(k_range, sse)
plt.xlabel('Number of clusters')
plt.ylabel('SSE')
plt.title('Elbow chart for KMeans clustering')
plt.show()

In [ ]:
models=[]  #initialize empty array to store models
R_squared_scores=[]
def linear_regression_on_clusters(x,y):
    
    for i in range(3):
        cluster_index= x[x['cluster'] == i].index      # getting the indexes of where cluster is i
        X = x.loc[cluster_index][['age', 'exp']]       # X representing age,exp features where data  belongs to cluster of i
        Y = y.loc[cluster_index]                       # Y representing target variable 'salary' where data belongs to cluster of i
        X_train,X_test,Y_train,Y_test=train_test_split(X,Y,test_size=0.2,random_state=0)  #split data for train and test 
        model = LinearRegression().fit(X_train,Y_train)
        r2=r2_score_(Y_test,model.predict(X_test))      # find R_squared score
        models.append(model)
        R_squared_scores.append(r2)
        

linear_regression_on_clusters(x,y)      #x and y are independent and dependent feature we splitted initially  